# Notebook 02b | Modelo Dimensional Gold

**Objetivos:**

- Carregar a camada Silver  
- Construir modelo dimensional com as dimensões de Data, Produto e Loja  
- Criar a tabela fato de vendas  
- Gravar as tabelas Gold em formato Delta  

## 1. Configuração do Ambiente

Inicializar Spark, importar funções e definir nomes de banco e caminhos no DBFS para a camada Gold.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import (
    col, to_date,
    year, month, dayofmonth, quarter, date_format
)

spark = SparkSession.builder.getOrCreate()

# Nomes de bancos e caminhos Gold no DBFS
silver_path       = "/FileStore/silver/sales_silver"
gold_db           = "gold"
gold_date_path    = "/FileStore/gold/dim_date"
gold_product_path = "/FileStore/gold/dim_product"
gold_store_path   = "/FileStore/gold/dim_store"
gold_fact_path    = "/FileStore/gold/fact_sales"
gold_customer_path = "/FileStore/gold/dim_customer"

## 2. Carregamento da Camada Silver

Ler a tabela Silver previamente criada para construir dimensões e fato.

In [0]:
# Carregar DataFrame da camada Silver diretamente do Delta Lake
sales_silver = spark.read.format("delta").load(silver_path)

# Garantir que 'order_date' está no tipo Date
sales_silver = sales_silver.withColumn("order_date", to_date(col("order_date")))

## 3. Criação da Dimensão de Data (`dim_date`)

Extrair todos os valores únicos de data e gerar atributos úteis e chave surrogate.


In [0]:
dim_date = (
    sales_silver
      .select(col("order_date").alias("date"))
      .distinct()
      .withColumn("date_key", date_format("date", "yyyyMMdd").cast("int"))
      .withColumn("year", year("date"))
      .withColumn("month", month("date"))
      .withColumn("day", dayofmonth("date"))
      .withColumn("quarter", quarter("date"))
)

## 4. Criação da Dimensão de Produto (`dim_product`)

Selecionar atributos de produto e remover duplicatas.

In [0]:
dim_product = (
    sales_silver
      .select(
          col("productkey").alias("product_key"),
          "category",
          "subcategory",
          "unit_price_usd",
          "unit_cost_usd"
      )
      .distinct()
)

## 5. Criação da Dimensão de Loja (`dim_store`)

Selecionar atributos de loja e remover duplicatas.

In [0]:
dim_store = (
    sales_silver
      .select(
          col("storekey").alias("store_key"),
          "country",
          "state",
          "square_meters"
      )
      .distinct()
)

## 6. Criação da Dimensão de Cliente (`dim_customer`)

Selecionar os atributos de cliente vindos da Silver, remover duplicatas e gerar a dimensão final com chave surrogate.


In [0]:
# Criar dimensão de cliente com os campos renomeados
dim_customer = (
    sales_silver
      .select(
          col("customerkey").alias("customer_key"),
          col("cust_gender").alias("gender"),
          col("cust_city").alias("city"),
          col("cust_state").alias("state"),
          col("cust_country").alias("country"),
          col("cust_birthday").alias("birthday")
      )
      .dropna(subset=["customer_key"])
      .dropDuplicates(["customer_key"])
)

## 6. Criação da Tabela Fato (`fact_sales`)

Combinar a Silver com as chaves das dimensões e manter as métricas de vendas.

In [0]:
fact_sales = (
    sales_silver
      .withColumn("date_key", date_format("order_date", "yyyyMMdd").cast("int"))
      .withColumnRenamed("productkey", "product_key")
      .withColumnRenamed("storekey", "store_key")
      .withColumnRenamed("customerkey", "customer_key")
      .select(
          "date_key",
          "product_key",
          "store_key",
          "customer_key",
          "quantity",
          "total_sales_usd",
          "total_cost_usd"
      )
)

## 7. Escrita das Tabelas Gold

Gravar as dimensões e a tabela fato em formato Delta e registrar no catálogo SQL.


In [0]:
# Criar database Gold
spark.sql(f"CREATE DATABASE IF NOT EXISTS {gold_db}")

# Dimensão Data
dim_date.write \
    .format("delta") \
    .mode("overwrite") \
    .option("mergeSchema", "true") \
    .save(gold_date_path)

spark.sql(f"DROP TABLE IF EXISTS {gold_db}.dim_date")
spark.sql(f"""
  CREATE TABLE {gold_db}.dim_date
  USING DELTA
  LOCATION '{gold_date_path}'
""")

# Dimensão Produto
dim_product.write \
    .format("delta") \
    .mode("overwrite") \
    .option("mergeSchema", "true") \
    .save(gold_product_path)

spark.sql(f"DROP TABLE IF EXISTS {gold_db}.dim_product")
spark.sql(f"""
  CREATE TABLE {gold_db}.dim_product
  USING DELTA
  LOCATION '{gold_product_path}'
""")

# Dimensão Loja
dim_store.write \
    .format("delta") \
    .mode("overwrite") \
    .option("mergeSchema", "true") \
    .save(gold_store_path)

spark.sql(f"DROP TABLE IF EXISTS {gold_db}.dim_store")
spark.sql(f"""
  CREATE TABLE {gold_db}.dim_store
  USING DELTA
  LOCATION '{gold_store_path}'
""")

# Dimensão Cliente
dim_customer.write \
    .format("delta") \
    .mode("overwrite") \
    .option("mergeSchema", "true") \
    .save(gold_customer_path)

spark.sql(f"DROP TABLE IF EXISTS {gold_db}.dim_customer")
spark.sql(f"""
  CREATE TABLE {gold_db}.dim_customer
  USING DELTA
  LOCATION '{gold_customer_path}'
""")

# Tabela Fato
fact_sales.write \
    .format("delta") \
    .mode("overwrite") \
    .option("mergeSchema", "true") \
    .save(gold_fact_path)

spark.sql(f"DROP TABLE IF EXISTS {gold_db}.fact_sales")
spark.sql(f"""
  CREATE TABLE {gold_db}.fact_sales
  USING DELTA
  LOCATION '{gold_fact_path}'
""")


Out[106]: DataFrame[]

## 8. Verificação Final

Conferir esquemas, algumas amostras e contagens para garantir que as tabelas foram criadas corretamente.

In [0]:
# Dimensão Data
dim_date.printSchema()
dim_date.show(5, truncate=False)
print("Total dates:", dim_date.count())

# Dimensão Produto
dim_product.printSchema()
dim_product.show(5, truncate=False)
print("Total products:", dim_product.count())

# Dimensão Loja
dim_store.printSchema()
dim_store.show(5, truncate=False)
print("Total stores:", dim_store.count())

# Dimensão Cliente
dim_store.printSchema()
dim_store.show(5, truncate=False)
print("Total customers:", dim_customer.count())

# Tabela Fato
fact_sales.printSchema()
fact_sales.show(5, truncate=False)
print("Total fact rows:", fact_sales.count())

root
 |-- date: date (nullable = true)
 |-- date_key: integer (nullable = true)
 |-- year: integer (nullable = true)
 |-- month: integer (nullable = true)
 |-- day: integer (nullable = true)
 |-- quarter: integer (nullable = true)

+----------+--------+----+-----+---+-------+
|date      |date_key|year|month|day|quarter|
+----------+--------+----+-----+---+-------+
|2016-03-01|20160301|2016|3    |1  |1      |
|2016-04-25|20160425|2016|4    |25 |2      |
|2016-05-03|20160503|2016|5    |3  |2      |
|2016-07-26|20160726|2016|7    |26 |3      |
|2016-08-15|20160815|2016|8    |15 |3      |
+----------+--------+----+-----+---+-------+
only showing top 5 rows

Total dates: 1641
root
 |-- product_key: integer (nullable = true)
 |-- category: string (nullable = true)
 |-- subcategory: string (nullable = true)
 |-- unit_price_usd: double (nullable = true)
 |-- unit_cost_usd: double (nullable = true)

+-----------+-----------------------------+--------------+--------------+-------------+
|product

## 9. Visualização e Exportação Interativa das Tabelas Gold

Exportar os dados das tabelas Gold diretamente pela interface do notebook (Databricks)


In [0]:
# Dimensão Data
dim_date_df = spark.table("gold.dim_date")
display(dim_date_df)

# Dimensão Produto
dim_product_df = spark.table("gold.dim_product")
display(dim_product_df)

# Dimensão Loja
dim_store_df = spark.table("gold.dim_store")
display(dim_store_df)

# Dimensão Cliente
dim_customer_df = spark.table("gold.dim_customer")
display(dim_customer_df)



date date_key year month day quarter 2016-03-01 20160301 2016 3 1 1 2017-08-11 20170811 2017 8 11 3 2017-09-11 20170911 2017 9 11 3 2018-05-28 20180528 2018 5 28 2 2018-08-10 20180810 2018 8 10 3 2019-05-08 20190508 2019 5 8 2 2019-06-04 20190604 2019 6 4 2 2020-08-24 20200824 2020 8 24 3 2021-01-27 20210127 2021 1 27 1 2016-04-25 20160425 2016 4 25 2 2017-01-06 20170106 2017 1 6 1 2018-03-17 20180317 2018 3 17 1 2018-06-06 20180606 2018 6 6 2 2019-09-22 20190922 2019 9 22 3 2019-11-01 20191101 2019 11 1 4 2019-11-18 20191118 2019 11 18 4 2020-01-21 20200121 2020 1 21 1 2020-07-24 20200724 2020 7 24 3 2020-08-05 20200805 2020 8 5 3 2016-05-03 20160503 2016 5 3 2 2016-07-26 20160726 2016 7 26 3 2016-08-15 20160815 2016 8 15 3 2016-08-31 20160831 2016 8 31 3 2016-10-03 20161003 2016 10 3 4 2018-06-26 20180626 2018 6 26 2 2018-08-08 20180808 2018 8 8 3 2018-08-11 20180811 2018 8 11 3 2018-09-01 20180901 2018 9 1 3 2018-09-09 20180909 2018 9 9 3 2018-10-05 20181005 2018 10 5 4 2018-11-02 20181102 2018 11 2 4 2019-11-21 20191121 2019 11 21 4 2020-04-30 20200430 2020 4 30 2 2020-08-28 20200828 2020 8 28 3 2020-08-29 20200829 2020 8 29 3 2016-01-28 20160128 2016 1 28 1 2017-01-27 20170127 2017 1 27 1 2017-02-26 20170226 2017 2 26 1 2017-09-28 20170928 2017 9 28 3 2018-06-30 20180630 2018 6 30 2 2019-05-27 20190527 2019 5 27 2 2016-07-17 20160717 2016 7 17 3 2016-11-08 20161108 2016 11 8 4 2016-12-19 20161219 2016 12 19 4 2017-01-24 20170124 2017 1 24 1 2018-11-01 20181101 2018 11 1 4 2019-02-23 20190223 2019 2 23 1 2020-03-07 20200307 2020 3 7 1 2020-03-13 20200313 2020 3 13 1 2020-09-24 20200924 2020 9 24 3 2020-12-18 20201218 2020 12 18 4 2016-07-03 20160703 2016 7 3 3 2016-08-23 20160823 2016 8 23 3 2017-06-29 20170629 2017 6 29 2 2017-09-29 20170929 2017 9 29 3 2020-02-04 20200204 2020 2 4 1 2020-02-15 20200215 2020 2 15 1 2017-02-16 20170216 2017 2 16 1 2017-07-31 20170731 2017 7 31 3 2018-05-26 20180526 2018 5 26 2 2018-09-08 20180908 2018 9 8 3 2019-01-07 20190107 2019 1 7 1 2019-01-08 20190108 2019 1 8 1 2020-05-23 20200523 2020 5 23 2 2021-02-15 20210215 2021 2 15 1 2016-02-04 20160204 2016 2 4 1 2016-05-26 20160526 2016 5 26 2 2016-06-02 20160602 2016 6 2 2 2017-08-14 20170814 2017 8 14 3 2017-08-18 20170818 2017 8 18 3 2017-10-23 20171023 2017 10 23 4 2017-12-02 20171202 2017 12 2 4 2019-01-28 20190128 2019 1 28 1 2019-10-05 20191005 2019 10 5 4 2017-12-25 20171225 2017 12 25 4 2018-08-31 20180831 2018 8 31 3 2019-01-30 20190130 2019 1 30 1 2019-03-14 20190314 2019 3 14 1 2019-03-17 20190317 2019 3 17 1 2019-04-28 20190428 2019 4 28 2 2019-07-30 20190730 2019 7 30 3 2020-02-12 20200212 2020 2 12 1 2020-12-17 20201217 2020 12 17 4 2016-01-13 20160113 2016 1 13 1 2016-09-23 20160923 2016 9 23 3 2017-02-28 20170228 2017 2 28 1 2017-09-21 20170921 2017 9 21 3 2018-01-23 20180123 2018 1 23 1 2021-01-18 20210118 2021 1 18 1 2021-01-25 20210125 2021 1 25 1 2016-01-01 20160101 2016 1 1 1 2016-06-16 20160616 2016 6 16 2 2016-09-30 20160930 2016 9 30 3 2017-08-10 20170810 2017 8 10 3 2018-02-26 20180226 2018 2 26 1 2021-02-02 20210202 2021 2 2 1 2016-01-19 20160119 2016 1 19 1 2017-06-30 20170630 2017 6 30 2 2017-08-19 20170819 2017 8 19 3 2017-12-08 20171208 2017 12 8 4 2018-09-18 20180918 2018 9 18 3 2019-05-14 20190514 2019 5 14 2 2019-07-08 20190708 2019 7 8 3 2019-07-28 20190728 2019 7 28 3 2019-10-24 20191024 2019 10 24 4 2020-09-07 20200907 2020 9 7 3 2016-05-09 20160509 2016 5 9 2 2016-07-19 20160719 2016 7 19 3 2017-01-30 20170130 2017 1 30 1 2017-07-06 20170706 2017 7 6 3 2018-07-28 20180728 2018 7 28 3 2018-09-24 20180924 2018 9 24 3 2019-12-28 20191228 2019 12 28 4 2020-05-08 20200508 2020 5 8 2 2016-09-15 20160915 2016 9 15 3 2017-05-11 20170511 2017 5 11 2 2018-04-26 20180426 2018 4 26 2 2018-05-27 20180527 2018 5 27 2 2018-10-04 20181004 2018 10 4 4 2019-06-24 20190624 2019 6 24 2 2019-12-10 20191210 2019 12 10 4 2016-02-08 20160208 2016 2 8 1 2016-10-07 20161007 2016 10 7 4 2016-12-12 20161212 2016 12 12 4 2018-12-25

product_key category subcategory unit_price_usd unit_cost_usd 1597 Music, Movies and Audio Books Movie DVD 57.88 26.62 2068 Home Appliances Microwaves 199.99 91.97 1707 Games and Toys Download Games 70.13 32.25 1657 Music, Movies and Audio Books Movie DVD 179.99 82.77 1986 Home Appliances Microwaves 139.99 71.37 361 Computers Laptops 389.0 198.32 435 Computers Desktops 269.95 137.63 2101 Home Appliances Water Heaters 877.5 403.53 639 Computers Projectors & Screens 459.0 152.08 1925 Home Appliances Refrigerators 279.99 142.75 810 Computers Computers Accessories 19.95 9.17 387 Computers Laptops 699.0 321.44 2003 Home Appliances Microwaves 179.99 82.77 1870 Home Appliances Washers & Dryers 1599.0 815.22 684 Computers Printers, Scanners & Fax 160.0 73.58 2416 Home Appliances Fans 73.99 34.03 830 Computers Computers Accessories 29.95 15.27 2272 Home Appliances Lamps 268.5 123.47 2311 Home Appliances Lamps 339.0 155.89 39 Audio MP4&MP3 299.23 99.14 1629 Music, Movies and Audio Books Movie DVD 9.99 5.09 451 Computers Desktops 559.0 257.06 169 TV and Video VCD & DVD 119.0 54.72 835 Computers Computers Accessories 52.9 26.97 1316 Cell phones Home & Office Phones 9.99 5.09 509 Computers Monitors 139.0 70.87 322 TV and Video Car Video 369.0 169.69 1277 Cameras and camcorders Cameras & Camcorders Accessories 52.13 26.58 2222 Home Appliances Lamps 635.99 210.72 2175 Home Appliances Coffee Machines 129.9 66.23 796 Computers Computers Accessories 16.9 8.62 2006 Home Appliances Microwaves 94.99 48.43 2030 Home Appliances Microwaves 94.99 48.43 1644 Music, Movies and Audio Books Movie DVD 57.88 26.62 1862 Home Appliances Washers & Dryers 2652.9 878.96 1611 Music, Movies and Audio Books Movie DVD 159.99 73.57 2036 Home Appliances Microwaves 94.99 48.43 139 TV and Video Televisions 499.99 229.93 598 Computers Projectors & Screens 109.0 55.57 1368 Cell phones Home & Office Phones 40.19 18.48 33 Audio MP4&MP3 255.0 84.49 1828 Home Appliances Washers & Dryers 1989.0 914.67 271 TV and Video Home Theater System 489.0 224.87 2485 Home Appliances Fans 400.0 183.95 2474 Home Appliances Fans 29.99 15.29 961 Cameras and camcorders Digital Cameras 165.0 75.88 190 TV and Video VCD & DVD 56.9 29.01 1863 Home Appliances Washers & Dryers 1989.9 915.08 1044 Cameras and camcorders Digital SLR Cameras 627.0 207.74 1739 Games and Toys Download Games 28.0 14.28 1773 Games and Toys Download Games 43.0 21.92 23 Audio MP4&MP3 134.0 61.62 2293 Home Appliances Lamps 29.99 15.29 2103 Home Appliances Water Heaters 508.0 258.99 1591 Music, Movies and Audio Books Movie DVD 12.66 5.82 1687 Games and Toys Boxed Games 6.88 3.16 1231 Cameras and camcorders Camcorders 1500.0 496.98 140 TV and Video Televisions 499.99 229.93 343 Computers Laptops 1099.0 364.12 531 Computers Monitors 679.0 224.97 1923 Home Appliances Refrigerators 493.0 226.71 1040 Cameras and camcorders Digital Cameras 198.0 91.05 844 Computers Computers Accessories 26.9 13.71 784 Computers Computers Accessories 16.5 7.59 321 TV and Video Car Video 329.0 151.3 1779 Games and Toys Download Games 43.0 21.92 427 Computers Desktops 469.0 215.68 2245 Home Appliances Lamps 29.99 15.29 12 Audio MP4&MP3 77.68 35.72 225 TV and Video Home Theater System 699.0 321.44 631 Computers Projectors & Screens 190.0 87.37 2426 Home Appliances Fans 39.99 20.39 2399 Home Appliances Air Conditioners 429.99 197.74 887 Computers Computers Accessories 50.0 25.49 2237 Home Appliances Lamps 29.99 15.29 2112 Home Appliances Water Heaters 791.0 363.75 1222 Cameras and camcorders Camcorders 431.0 219.74 1896 Home Appliances Washers & Dryers 999.0 509.32 1347 Cell phones Home & Office Phones 21.0 9.66 551 Computers Projectors & Screens 2295.0 760.38 656 Computers Printers, Scanners & Fax 158.0 72.66 280 TV and Video Home Theater System 329.0 167.73 2441 Home Appliances Fans 9.99 5.09 127 TV and Video Televisions 143.4 73.11 2494 Cell phones Cell phones Accessories 2.94 1.5 168 TV and Video VCD & DVD 129.0 59.32 847 Computers Computers Accessori

store_key country state square_meters 20 Germany Brandenburg 1715 37 United Kingdom Ayrshire 2100 21 Germany Freie Hansestadt Bremen 560 61 United States South Carolina 2000 9 Canada Northwest Territories 1500 55 United States Nevada 2000 51 United States Maine 1295 14 France Franche-Comté 350 36 United Kingdom Armagh 1300 23 Germany Hamburg 1365 0 Online Online null 5 Australia Victoria 2000 45 United States Connecticut 2000 18 France Mayotte 310 39 United Kingdom Blaenau Gwent 2100 32 Netherlands Flevoland 910 41 United Kingdom Fermanagh 2100 50 United States Kansas 2000 15 France La Réunion 400 2 Australia Northern Territory 665 38 United Kingdom Belfast 1800 29 Italy Enna 1000 34 Netherlands Groningen 1365 30 Italy Pesaro 2100 43 United States Alaska 1190 57 United States New Mexico 1645 54 United States Nebraska 2000 13 France Corse 245 28 Italy Caltanissetta 1200 19 Germany Berlin 1295 44 United States Arkansas 2000 31 Netherlands Drenthe 1085 47 United States Hawaii 1120 59 United States Oregon 2000 49 United States Iowa 2000 8 Canada Newfoundland and Labrador 2105 66 United States Wyoming 840 12 France Basse-Normandie 350 33 Netherlands Friesland 1540 16 France Limousin 385 62 United States South Dakota 1120 26 Germany Saarland 350 53 United States Montana 1260 56 United States New Hampshire 1260 27 Germany Sachsen-Anhalt 2000 63 United States Utah 2000 1 Australia Australian Capital Territory 595 42 United Kingdom North Down 1900 64 United States Washington DC 1330 17 France Martinique 350 22 Germany Freistaat Thüringen 2000 24 Germany Hessen 1855 4 Australia Tasmania 2000 6 Australia Western Australia 2000 40 United Kingdom Dungannon and South Tyrone 1300 48 United States Idaho 1540 65 United States West Virginia 1785 10 Canada Nunavut 1210

customer_key gender city state country birthday 301 Female WANDEARAH EAST South Australia Australia 1939-07-03 325 Female MOUNT BUDD Western Australia Australia 1979-09-27 554 Female WINJALLOK Victoria Australia 1947-05-26 1042 Male TAWONGA SOUTH Victoria Australia 1965-11-19 1314 Male EDITH RIVER Northern Territory Australia 1965-12-21 1568 Male KOTTA Victoria Australia 1975-07-25 1585 Female GREEN LAKE Victoria Australia 1990-08-12 1626 Female NEDS CORNER Victoria Australia 1985-10-17 1642 Female TARLO New South Wales Australia 1965-03-03 1863 Female NAMBOUR DC Queensland Australia 1984-09-22 2238 Female BRUCKNELL Victoria Australia 1969-10-31 2248 Male JUNG Victoria Australia 1987-12-15 2435 Female BLAKEBROOK New South Wales Australia 1968-04-01 2469 Female BIDWILL Queensland Australia 1948-05-20 2512 Female BUNKERS HILL Victoria Australia 1992-11-13 2792 Male BAMGANIE Victoria Australia 1976-08-25 3002 Male SMITHTON Tasmania Australia 2000-11-08 3203 Male ARGENTON New South Wales Australia 1998-08-18 3327 Female KONONGWOOTONG Victoria Australia 1948-04-28 3575 Male HOPPERS CROSSING Victoria Australia 1942-03-04 3964 Female DIXIE Victoria Australia 1944-02-16 4174 Female OCEAN REEF Western Australia Australia 1990-10-05 5097 Female Mount Pleasant Queensland Australia 1942-11-13 5445 Male REEFTON Victoria Australia 1952-09-10 5962 Male SWAN BAY New South Wales Australia 1938-11-17 6258 Male SANDFORD Victoria Australia 1976-07-03 6308 Male KOOREH Victoria Australia 2001-02-15 7109 Male LANKEYS CREEK New South Wales Australia 1979-11-15 7566 Male KILLARA Victoria Australia 1993-07-01 7700 Male STANWELL TOPS New South Wales Australia 1975-01-27 7783 Female MOUNT WALLACE Victoria Australia 1961-08-13 8098 Female SOUTH GREENOUGH Western Australia Australia 1967-01-26 8181 Female DARTMOUTH Victoria Australia 1985-07-08 8789 Female KALKARINDJI Northern Territory Australia 1999-07-13 8945 Female WARUMBUL New South Wales Australia 1939-06-28 9167 Male PARACOMBE South Australia Australia 1975-12-02 9184 Male CORUNNUN Victoria Australia 1964-11-24 9456 Male CLAREDALE Queensland Australia 1941-05-21 9812 Female MINJARY New South Wales Australia 1953-01-23 9915 Female SEPPINGS Western Australia Australia 1991-11-10 10039 Female NIKENBAH Queensland Australia 1947-10-22 10299 Male BEELBANGERA New South Wales Australia 1937-05-27 10393 Male ROSENTHAL HEIGHTS Queensland Australia 1981-11-29 11035 Female KINGS FOREST New South Wales Australia 1939-12-08 12160 Male Oakhurst New South Wales Australia 1956-09-05 12365 Female STEEPLE FLAT New South Wales Australia 1958-04-06 12392 Female GREENHILL South Australia Australia 1957-03-08 12649 Female NOBLE PARK NORTH Victoria Australia 1965-12-11 12729 Male STANNUM New South Wales Australia 1937-10-14 12859 Male NABAWA Western Australia Australia 1942-04-29 13045 Female BLUE MOUNTAIN HEIGHTS Queensland Australia 1957-10-19 13071 Female CUBALLING Western Australia Australia 1973-06-28 13365 Male MOONEM New South Wales Australia 1961-01-02 14069 Male ROB ROY New South Wales Australia 1949-05-24 14180 Female KALGOORLIE Western Australia Australia 1998-05-14 14906 Female BOYER Tasmania Australia 1982-11-16 14962 Female Crestwood New South Wales Australia 1936-04-05 14988 Female WYNDHAM VALE Victoria Australia 1958-07-24 15391 Female MARRAWEENEY Victoria Australia 1989-01-25 15718 Female DAKENBA Queensland Australia 1957-02-20 16716 Female KAYUGA New South Wales Australia 1987-12-16 17412 Male VICTORIA PARK Western Australia Australia 1969-08-31 17811 Female WATTLE GLEN Victoria Australia 1985-10-15 18309 Male FYANS CREEK Victoria Australia 1992-01-07 18470 Male GOSFORD New South Wales Australia 1969-03-12 18493 Male TASCOTT New South Wales Australia 1994-09-27 18887 Female BOOROLITE Victoria Australia 1978-11-25 19082 Male RANSOME Queensland Australia 1939-04-06 19207 Male KURRACA Victoria Australia 1991-01-19 19404 Male WYNNUM Queensland Australia 1997-06-10 19534 Female TOOBORAC Victoria Australia 1964

In [0]:
# Tabela Fato
fact_sales_df = spark.table("gold.fact_sales")
display(fact_sales_df)

date_key product_key store_key quantity total_sales_usd total_cost_usd customer_key 20160101 1304 10 1 68.0 31.27 265598 20160101 1048 0 2 854.0 282.94 1269051 20160101 2007 0 1 665.94 220.64 1269051 20160101 1106 0 7 2254.0 1036.5600000000002 266019 20160101 373 0 1 326.0 166.2 266019 20160101 1080 0 4 2584.0 856.12 266019 20160101 163 38 6 9553.2 3165.18 1107461 20160101 1529 38 2 510.0 234.54 1107461 20160101 421 33 4 1876.0 862.72 844003 20160101 1617 43 1 57.99 26.67 2035771 20160101 666 43 5 815.0 374.79999999999995 2035771 20160101 1154 29 9 8982.0 2975.94 759705 20160101 2510 29 1 4.06 2.07 759705 20160101 1060 29 5 3135.0 1038.7 759705 20160101 1648 9 1 109.99 56.08 254540 20160101 618 0 5 1495.0 495.3 370077 20160101 128 66 7 1003.8000000000001 511.77 1984985 20160101 1638 66 1 13.89 6.39 1984985 20160101 1634 66 1 9.99 5.09 1984985 20160101 2392 66 3 1289.97 593.22 1984985 20160101 1807 65 1 32.0 16.31 1977527 20160101 1594 65 4 39.96 20.36 1977527 20160101 1297 65 1 25.0 11.5 1977527 20160101 1654 41 5 1299.95 430.7 1187306 20160101 123 0 1 279.99 128.76 738549 20160101 1700 0 2 17.76 8.16 738549 20160101 1253 63 7 139.92999999999998 71.33 1982762 20160102 1176 56 1 1000.0 331.32 1438050 20160102 153 40 2 939.94 432.24 980164 20160102 136 56 1 349.95 160.93 1853699 20160102 1637 56 4 71.96 33.08 1853699 20160102 1691 0 1 5.39 2.75 758280 20160102 319 0 2 1738.0 575.84 758280 20160102 1674 0 8 55.92 28.48 758280 20160102 2511 0 9 36.54 18.63 758280 20160102 1720 0 2 140.26 64.5 758280 20160102 1597 0 7 405.16 186.34 758280 20160102 784 0 1 16.5 7.59 758280 20160102 2445 18 3 14.97 7.62 693285 20160102 65 57 7 1267.0 582.68 1730985 20160102 1432 57 9 2700.0 1241.64 1730985 20160102 1951 28 3 9599.97 3180.66 763246 20160102 934 57 1 79.0 36.33 1512558 20160102 930 57 8 271.92 138.64 1512558 20160102 1436 57 5 1290.0 593.25 1512558 20160102 1547 57 3 765.0 351.81 1512558 20160102 53 57 5 1480.0 490.34999999999997 1512558 20160102 917 66 1 179.0 59.31 1322959 20160102 39 66 1 299.23 99.14 1322959 20160102 39 22 1 299.23 99.14 507981 20160102 1653 9 5 549.9499999999999 280.4 209990 20160102 145 9 3 8699.97 2882.46 209990 20160102 1733 31 2 45.58 23.24 815458 20160102 41 31 6 1392.0 640.14 815458 20160102 1184 56 3 2670.0 1227.84 1839627 20160102 2296 42 7 1879.5 864.29 911025 20160102 1487 63 1 267.0 122.78 1633409 20160102 558 63 7 2093.0 693.4200000000001 1633409 20160102 206 63 3 1707.0 784.98 1633409 20160102 1203 47 4 3920.0 1298.76 1612400 20160102 1245 59 2 336.0 171.3 1301565 20160102 1973 59 4 1119.96 571.0 1301565 20160102 731 59 4 516.0 237.28 1301565 20160102 1947 29 2 986.0 453.42 793573 20160102 1645 29 7 405.16 186.34 793573 20160102 371 29 7 4193.0 1928.2199999999998 793573 20160102 448 29 6 1619.3999999999999 825.5999999999999 799366 20160102 1975 29 1 3199.99 1060.22 799366 20160102 1445 10 4 1072.0 492.96 243917 20160102 1624 10 6 1314.0 435.36 243917 20160102 1615 10 2 579.98 192.16 243917 20160102 1596 42 1 12.66 5.82 942807 20160102 1253 42 7 139.92999999999998 71.33 942807 20160102 663 42 3 744.0 246.51 942807 20160102 1194 42 6 3798.0 1746.54 942807 20160102 1139 2 5 1640.0 754.2 129318 20160102 1031 2 2 330.0 151.76 129318 20160102 302 50 8 7992.0 2647.92 1713253 20160102 2105 50 5 7375.0 2443.5 1713253 20160102 1608 56 1 109.99 56.08 1736623 20160102 1641 56 2 25.32 11.64 1736623 20160102 1574 56 3 179.97 82.77 1736623 20160102 2218 53 2 239.98 122.34 1836599 20160102 78 53 1 40.55 18.65 1836599 20160102 2451 53 3 89.97 45.87 1482586 20160102 1645 53 1 57.88 26.62 1482586 20160102 1728 53 2 159.6 73.4 1482586 20160102 976 0 1 188.0 86.45 607356 20160102 2017 0 3 299.96999999999997 152.94 607356 20160102 1607 66 1 179.99 82.77 1260533 20160102 1223 66 7 3220.0 1641.64 1260533 20160102 2010 51 7 979.9300000000001 499.59000000000003 1843882 20160102 426 51 1 499.9 254.86 1843882 20160102 120 0 3 359.96999999999997 183.51 909014 20160102 382 0 2 765.9 390.48 909014 20160102 1722 0 3 168.0 85.65 9090

## 9. Próximos Passos

- Exportar e conectar o Power BI a estas tabelas Gold (`dim_date`, `dim_product`, `dim_store`, `fact_sales`).
- No Power BI, estabelecer os relacionamentos entre a tabela fato e as dimensões:
    - `fact_sales.date_key` → `dim_date.date_key`
    - `fact_sales.product_key` → `dim_product.product_key`
    - `fact_sales.store_key` → `dim_store.store_key`
- Construir dashboard e relatórios para análise de desempenho de vendas.